# Analyzing avalnche weather from SNOTEL sites

## Importing libraries

In [1]:
import numpy as np
import pandas as pd
import netCDF4 as nc
import glob
import os
import numpy.ma as ma
import math
from netCDF4 import stringtochar

## Create a nested list of variables that contain the snotel sites for each avalanche

In [2]:

#Initialize variables
counter = 2555 # 7 years in days

meta_data = pd.read_csv('D:/UC DAVIS/CW3E/data/avalanche_data/snotel_meta_data.csv')
avalanche_data = pd.read_csv('D:/UC DAVIS/CW3E/data/avalanche_data/avalanche_coords_datenum.csv')

master_list = []
location = []
def euclidean(x1,x2,y1,y2):
    y2=abs(y2)
    y1=abs(y1)
    x2=abs(x2)
    x1=abs(x1)
    
    length = ((y2-y1)**2 + (x2-x1)**2)**0.5
    return length

for i in range(len(avalanche_data)):
    sites = []
    for j in range(len(meta_data)):
        ava_lat = float(avalanche_data.loc[i][2])
        ava_lon = float(avalanche_data.loc[i][3])
        site_lat = meta_data.loc[j][6]
        site_lon = meta_data.loc[j][7]
        
        dist = euclidean(ava_lat, site_lat, ava_lon, site_lon)
        
        if dist < 1.0:
            sites.append(meta_data.loc[j][10])
            
        else:
            pass

    master_list.append(sites)
    location.append(avalanche_data.loc[i][4])

avalanche_data['snotel_sites'] = master_list


## Remove avalanches with no sites

In [3]:
for i in range(len(avalanche_data['snotel_sites'])):
    if len(avalanche_data['snotel_sites'][i]) == 0:
        avalanche_data = avalanche_data.drop(index = [i])
    else:
        pass
    
#reset the index
avalanche_data = avalanche_data.reset_index(drop=True)

yt
yt
yt
yt
yt
yt


state   date    lat     lon  \
0      AK  16410  63.32 -145.66   
1      AK  16761  61.78 -149.30   
2      AK  16902  63.14 -145.55   
3      AK  16894  63.14 -145.55   
4      AK  16858  61.61 -146.65   
..    ...    ...    ...     ...   
131    WY  18353  43.53 -110.98   
132    WY  18614  42.58 -110.75   
133    WY  18680  43.70 -110.79   
134    WY  18676  43.75 -110.06   
135    WY  18675  43.09 -110.92   

                                             site_name  \
0                      Rainbow Ridge area, Delta Range   
1                          Eldorado Bowl, Hatcher Pass   
2               Summit Lake area, Eastern Alaska Range   
3               Summit Lake area, Eastern Alaska Range   
4                                Nelchina Glacier area   
..                                                 ...   
131           Taylor Mountain, northwest of Teton Pass   
132                  Near Sheep Pass, Salt River Range   
133  Broken Thumb Couloir, Peak 9,975 (25 Short), G...   
134                                  Togwotee Pass, WY   
135     Squaw Creek Drainage, Southeast of Alpine, WY    

                                          snotel_sites  
0                                    [2222, 1268, 963]  
1    [641, 953, 2044, 1070, 1035, 967, 1002, 946, 1...  
2                                    [2222, 1268, 963]  
3                                    [2222, 1268, 963]  
4                                               [1095]  
..                                                 ...  
131  [1082, 764, 695, 497, 816, 460, 831, 419, 546,...  
132  [1114, 497, 460, 509, 555, 661, 831, 419, 471,...  
133  [1082, 944, 764, 695, 497, 816, 460, 555, 831,...  
134  [1130, 1082, 944, 764, 497, 807, 816, 460, 555...  
135  [1082, 695, 497, 460, 509, 555, 661, 831, 419,...  

[136 rows x 6 columns]

## Checking the percentage of missing date

In [7]:
# file with all SNOTEL sites

path = 'D:/UC DAVIS/CW3E/data/avalanche_data/nc_Data1/'
mega_file_list = os.listdir(path)

percent_missing_list = []

In [5]:
for k in range(len(mega_file_list)):
    
    ncfile = mega_file_list[k]
    final = ("".join([path, ncfile]))
    ds = nc.Dataset(final)

    start = len(ds['Date']) - counter
    print(len(ds['Date']))
    if start < 0:
        start = 0
    else:
        pass

    # flip the dates, since we know that they all end on the same day
    site_dates = np.flip(ds['Date'][start:])
    SWE = np.flip(ds['SWE'][start:])
    temp_max = np.flip(ds['Temp_Max'][start:])
    temp_min = np.flip(ds['Temp_Min'][start:])
    precip = np.flip(ds['Precipitation'][start:])
    cum_precip = np.flip(ds['Cumulative_Precipitation'][start:])
    lat = ds['Latitude'][start:]
    lon = ds['Longitude'][start:]
    
    dictionary = {'Date':site_dates,'SWE':SWE,'Temp_Max':temp_max,'Temp_Min':temp_min,
                  'Precipitation':precip,'Cumulative_Precipitation':cum_precip,
                  'Latitude':lat,'Longitude':lon}
    df = pd.DataFrame(dictionary, columns =['Date', 'SWE', 'Temp_Max', 'Temp_Min', 
                             'Precipitation', 'Cumulative_Precipitation',
                             'Latitude','Longitude'])

    # Only check SWE, temp_max, temp_min, ppt, cumulative_ppt
    cols =['SWE','Temp_Max', 'Temp_Min', 'Precipitation', 'Cumulative_Precipitation',]
    full = df.notnull().sum()['Date'] * 5
    null = 0
    not_null = 0
    for i in range(len(cols)):
        null = null + df.isnull().sum()[cols[i]]
        not_null = not_null + df.notnull().sum()[cols[i]]
        
    percent_present = np.round((not_null/full)*100,3)
    percent_missing = np.round((null/full)*100,3)
    
    percent_missing_list.append(percent_missing)
    #print('For ' + str(mega_file_list[k][:11]) + ' the percentage of missing data is ' + str(percent_missing) + '%')

1032
For snotel_2222 the percentage of missing data is 3.585%
3996
For snotel_1130 the percentage of missing data is 0.055%
13131
For snotel_555_ the percentage of missing data is 0.031%
14546
For snotel_493_ the percentage of missing data is 0.031%
14878
For snotel_418_ the percentage of missing data is 12.806%
14911
For snotel_544_ the percentage of missing data is 0.07%
14981
For snotel_683_ the percentage of missing data is 0.603%
15642
For snotel_435_ the percentage of missing data is 0.023%
14911
For snotel_468_ the percentage of missing data is 0.031%
15486
For snotel_730_ the percentage of missing data is 0.07%


## Append all the data into a mega dataframe

In [17]:
def euclidean(x1,x2,y1,y2):
    length = ((y2-y1)**2 + (x2-x1)**2)**0.5
    return length

In [13]:
df = pd.DataFrame(columns = ['State','Latitude', 'Longitude','Date','SWE', 'Precipitation', 'Cumulative_Precipitation',
                             'Max_Temp','Min_Temp','snotel_dist'])
#avalanche_length
for i in range(avalanche_length):
    ava_lat = avalanche_data['lat'][i]
    ava_lon = avalanche_data['lon'][i]

    for j in range(len(avalanche_data['snotel_sites'][i])):
        crying = 0
        fn1 = 'D:/UC DAVIS/CW3E/data/avalanche_data/nc_Data/snotel_'
        # this section refreshes the avalanche_id
        avalanche_id = str(avalanche_data['snotel_sites'][i][j])
        
        fn2 = ("".join([fn1, avalanche_id,'*']))
        final = os.path.normpath(glob.glob(fn2)[0])
        ds = nc.Dataset(final)
        start = len(ds['Date']) - counter

        if start < 0:
            start = 0
        else:
            pass

        # flip the dates, since we know that they all end on the same day
        site_dates = np.flip(ds['Date'][start:])
        SWE = np.flip(ds['SWE'][start:])
        temp_max = np.flip(ds['Temp_Max'][start:])
        temp_min = np.flip(ds['Temp_Min'][start:])
        precip = np.flip(ds['Precipitation'][start:])
        cum_precip = np.flip(ds['Cumulative_Precipitation'][start:])
        lat = ds['Latitude'][start:]
        lon = ds['Longitude'][start:]
        
        # Getting euclidean distance for each snotel_site
        dist = euclidean(ava_lon,lon[0],ava_lat,lat[0])
        
        max_length = len(site_dates)
        for k in range(max_length):
            # change the avalanche_data when converting to a loop
            if site_dates[k] == avalanche_data['date'][i]:
                exact = np.where(site_dates == site_dates[k])
                ava_index = exact[0]
                ava_index = ava_index[0]
                crying = 5
        if crying != 5:
            continue
        else:
            pass

        # 6 days before avlanche and 1 day after, note that the dates are flipped so the indexes might be wonky!
        lower = ava_index + 7
        upper = ava_index - 1
        index_period = np.arange(upper,lower,1)
        # Using these lat/lon as a placeholder for now

        for index in index_period:
            # lat, lon, date, SWE, Precipitation, Cumulative_Precipitation, Max_Temp, Min_Temp
            df = df.append({'State' : ds.getncattr('State'), 'Latitude' : lat[0], 'Longitude' : lon[0], 'Date': site_dates[index],
                            'SWE' : SWE[index], 'Precipitation' : precip[index], 'Cumulative_Precipitation' : cum_precip[index], 
                            'Max_Temp' : temp_max[index], 'Min_Temp' : temp_min[index], 
                            'snotel_dist' : dist}, ignore_index = True)
    

D:\UC DAVIS\CW3E\data\avalanche_data\nc_Data\snotel_2222_2018-09-30_2021-07-27.nc


<ipython-input-13-9679581d0a1c>:17: DeprecationWarning: tostring() is deprecated. Use tobytes() instead.
  print(ds)
<ipython-input-13-9679581d0a1c>:59: DeprecationWarning: tostring() is deprecated. Use tobytes() instead.
  df = df.append({'State' : ds.getncattr('State'), 'Latitude' : lat[0], 'Longitude' : lon[0], 'Date': site_dates[index],


<class 'netCDF4._netCDF4.Dataset'>
root group (NETCDF3_CLASSIC data model, file format NETCDF3):
    site_id: 2222.0
    State: AK
    Elevation: 558.0
    Start Date: 2018-09-30
    dimensions(sizes): Date(1032)
    variables(dimensions): float64 Date(Date), float64 Temp_Max(Date), float64 Temp_Min(Date), float64 SWE(Date), float64 Precipitation(Date), float64 Cumulative_Precipitation(Date), float64 Longitude(Date), float64 Latitude(Date)
    groups: 
D:\UC DAVIS\CW3E\data\avalanche_data\nc_Data\snotel_1268_2014-08-07_2021-07-27.nc
<class 'netCDF4._netCDF4.Dataset'>
root group (NETCDF3_CLASSIC data model, file format NETCDF3):
    site_id: 1268.0
    State: AK
    Elevation: 914.0
    Start Date: 2014-08-07
    dimensions(sizes): Date(2547)
    variables(dimensions): float64 Date(Date), float64 Temp_Max(Date), float64 Temp_Min(Date), float64 SWE(Date), float64 Precipitation(Date), float64 Cumulative_Precipitation(Date), float64 Longitude(Date), float64 Latitude(Date)
    groups: 
D:\U

## Save to your desktop!

In [15]:
df.to_csv(r'D:/UC DAVIS/CW3E/data/avalanche_data/avalanche_weather.csv', index = False)

## Saving each avalanche event into a netCDF file

### Use avalanche_data_dates dataframe as it contains the correct date format

In [88]:
for i in range(avalanche_length):
    df = pd.DataFrame(columns = ['State','Latitude', 'Longitude','Date','SWE', 'Precipitation', 'Cumulative_Precipitation',
                             'Max_Temp','Min_Temp'])
    for j in range(len(avalanche_data['snotel_sites'][i])):
        crying = 0
        fn1 = 'D:/UC DAVIS/CW3E/data/avalanche_data/nc_Data/snotel_'
        # this section refreshes the avalanche_id
        avalanche_id = str(avalanche_data['snotel_sites'][i][j])
        
        fn2 = ("".join([fn1, avalanche_id,'*']))
        final = os.path.normpath(glob.glob(fn2)[0])
        print(final)
        ds = nc.Dataset(final)
        print(ds)
        start = len(ds['Date']) - counter

        if start < 0:
            start = 0
        else:
            pass

        # flip the dates, since we know that they all end on the same day
        site_dates = np.flip(ds['Date'][start:])
        SWE = np.flip(ds['SWE'][start:])
        temp_max = np.flip(ds['Temp_Max'][start:])
        temp_min = np.flip(ds['Temp_Min'][start:])
        precip = np.flip(ds['Precipitation'][start:])
        cum_precip = np.flip(ds['Cumulative_Precipitation'][start:])
        lat = ds['Latitude'][start:]
        lon = ds['Longitude'][start:]
        
        max_length = len(site_dates)
        for k in range(max_length):
            # change the avalanche_data when converting to a loop
            if site_dates[k] == avalanche_data['date'][i]:
                exact = np.where(site_dates == site_dates[k])
                ava_index = exact[0]
                ava_index = ava_index[0]
                crying = 5
        if crying != 5:
            continue
        else:
            pass

        # 6 days before avlanche and 1 day after, note that the dates are flipped so the indexes might be wonky!
        lower = ava_index + 7
        upper = ava_index - 1
        index_period = np.arange(upper,lower,1)
        # Using these lat/lon as a placeholder for now

        for index in index_period:
            # lat, lon, date, SWE, Precipitation, Cumulative_Precipitation, Max_Temp, Min_Temp
            df = df.append({'State' : ds.getncattr('State'), 'Latitude' : lat[0], 'Longitude' : lon[0], 'Date': site_dates[index],
                            'SWE' : SWE[index], 'Precipitation' : precip[index], 'Cumulative_Precipitation' : cum_precip[index], 
                            'Max_Temp' : temp_max[index], 'Min_Temp' : temp_min[index]}, ignore_index = True)
    
    
    exact_date = site_dates[exact]
 
    fin = 'D:/UC DAVIS/CW3E/data/avalanche_data/nc_trial_final_one/_'
    
    s = avalanche_data_dates['date'][i]
    l = s.split('-')
    new_date = ("_".join([l[0], l[1],l[2]]))
    location = ds.getncattr('State')
    filename = ("".join([fin, new_date,'_',location,'.nc'])) 
    ncds = nc.Dataset(filename, 'w', format = 'NETCDF4')

    fill = 999
    # create dimensions
    date = ncds.createDimension('Date' , None)
    lat = ncds.createDimension('lat', None)
    lon = ncds.createDimension('lon', None)

    # create dimensions for avalanche weather data
    temp_max = ncds.createDimension('temp_max', None)
    temp_max = ncds.createDimension('temp_min', None)
    SWE = ncds.createDimension('SWE', None)
    precip = ncds.createDimension('precip', None)
    precip_cum = ncds.createDimension('precip_cum', None)

    # create variables for time and space
    dates = ncds.createVariable('date', 'i4', ('Date', ), fill_value= fill)
    lats = ncds.createVariable('lat', 'f4',('lat', ), fill_value= fill)
    lons = ncds.createVariable('lon', 'f4',('lon', ), fill_value= fill)

    # create variables for avalanche weather data
    temp_maxs = ncds.createVariable('temp_max', 'f4', ('temp_max', ), fill_value= fill)
    temp_mins = ncds.createVariable('temp_min', 'f4', ('temp_min', ), fill_value= fill)
    SWEs = ncds.createVariable('SWE', 'f4', ('SWE', ), fill_value= fill)
    precips = ncds.createVariable('precip', 'f4', ('precip', ), fill_value= fill)
    precip_cums = ncds.createVariable('precip_cum', 'f4', ('precip_cum', ), fill_value= fill)
    
    # Set global vars
    ncds.setncattr('Latitude',avalanche_data_dates['lat'][i])
    ncds.setncattr('Longitude',avalanche_data_dates['lon'][i])
    ncds.setncattr('Date',avalanche_data_dates['date'][i])

    # keying the data
    dates[:] = df['Date']
    lats[:] = df['Latitude']
    lons[:] = df['Longitude']
    temp_maxs[:] = df['Max_Temp']
    temp_mins[:] = df['Min_Temp']
    SWEs[:] = df['SWE']
    precips[:] = df['Precipitation']
    precip_cums[:] = df['Cumulative_Precipitation']

    ncds.close()

D:\UC DAVIS\CW3E\data\avalanche_data\nc_Data\snotel_641_2019-12-02_2021-07-21.nc
<class 'netCDF4._netCDF4.Dataset'>
root group (NETCDF3_CLASSIC data model, file format NETCDF3):
    site_id: 641.0
    State: AK
    Elevation: 823.0
    Start Date: 2019-12-02
    dimensions(sizes): Date(598)
    variables(dimensions): float64 Date(Date), float64 Temp_Max(Date), float64 Temp_Min(Date), float64 SWE(Date), float64 Precipitation(Date), float64 Cumulative_Precipitation(Date), float64 Longitude(Date), float64 Latitude(Date)
    groups: 
D:\UC DAVIS\CW3E\data\avalanche_data\nc_Data\snotel_953_2019-12-17_2021-07-21.nc
<class 'netCDF4._netCDF4.Dataset'>
root group (NETCDF3_CLASSIC data model, file format NETCDF3):
    site_id: 953.0
    State: AK
    Elevation: 70.0
    Start Date: 2019-12-17
    dimensions(sizes): Date(583)
    variables(dimensions): float64 Date(Date), float64 Temp_Max(Date), float64 Temp_Min(Date), float64 SWE(Date), float64 Precipitation(Date), float64 Cumulative_Precipitati

<ipython-input-88-66cc32d76007>:14: DeprecationWarning: tostring() is deprecated. Use tobytes() instead.
  print(ds)
<ipython-input-88-66cc32d76007>:53: DeprecationWarning: tostring() is deprecated. Use tobytes() instead.
  df = df.append({'State' : ds.getncattr('State'), 'Latitude' : lat[0], 'Longitude' : lon[0], 'Date': site_dates[index],



D:\UC DAVIS\CW3E\data\avalanche_data\nc_Data\snotel_1103_1972-10-01_2021-07-21.nc
<class 'netCDF4._netCDF4.Dataset'>
root group (NETCDF3_CLASSIC data model, file format NETCDF3):
    site_id: 1103.0
    State: AK
    Elevation: 469.0
    dimensions(sizes): Date(17826)
    variables(dimensions): float64 Date(Date), float64 Temp_Max(Date), float64 Temp_Min(Date), float64 SWE(Date), float64 Precipitation(Date), float64 Cumulative_Precipitation(Date), float64 Longitude(Date), float64 Latitude(Date)
    groups: 
D:\UC DAVIS\CW3E\data\avalanche_data\nc_Data\snotel_2222_2018-09-30_2021-07-21.nc
<class 'netCDF4._netCDF4.Dataset'>
root group (NETCDF3_CLASSIC data model, file format NETCDF3):
    site_id: 2222.0
    State: AK
    Elevation: 558.0
    Start Date: 2018-09-30
    dimensions(sizes): Date(1026)
    variables(dimensions): float64 Date(Date), float64 Temp_Max(Date), float64 Temp_Min(Date), float64 SWE(Date), float64 Precipitation(Date), float64 Cumulative_Precipitation(Date), float64 

<ipython-input-88-66cc32d76007>:66: DeprecationWarning: tostring() is deprecated. Use tobytes() instead.
  location = ds.getncattr('State')



<class 'netCDF4._netCDF4.Dataset'>
root group (NETCDF3_CLASSIC data model, file format NETCDF3):
    site_id: 963.0
    State: AK
    Elevation: 378.0
    dimensions(sizes): Date(12348)
    variables(dimensions): float64 Date(Date), float64 Temp_Max(Date), float64 Temp_Min(Date), float64 SWE(Date), float64 Precipitation(Date), float64 Cumulative_Precipitation(Date), float64 Longitude(Date), float64 Latitude(Date)
    groups: 
D:\UC DAVIS\CW3E\data\avalanche_data\nc_Data\snotel_2222_2018-09-30_2021-07-21.nc
<class 'netCDF4._netCDF4.Dataset'>
root group (NETCDF3_CLASSIC data model, file format NETCDF3):
    site_id: 2222.0
    State: AK
    Elevation: 558.0
    Start Date: 2018-09-30
    dimensions(sizes): Date(1026)
    variables(dimensions): float64 Date(Date), float64 Temp_Max(Date), float64 Temp_Min(Date), float64 SWE(Date), float64 Precipitation(Date), float64 Cumulative_Precipitation(Date), float64 Longitude(Date), float64 Latitude(Date)
    groups: 
D:\UC DAVIS\CW3E\data\avalanch

C:\Users\psle1\anaconda3\lib\site-packages\numpy\core\_asarray.py:83: UserWarning: Warning: converting a masked element to nan.
  return array(a, dtype, copy=False, order=order)



<class 'netCDF4._netCDF4.Dataset'>
root group (NETCDF3_CLASSIC data model, file format NETCDF3):
    site_id: 1002.0
    State: AK
    Elevation: 76.0
    Start Date: 1983-10-01
    dimensions(sizes): Date(11653)
    variables(dimensions): float64 Date(Date), float64 Temp_Max(Date), float64 Temp_Min(Date), float64 SWE(Date), float64 Precipitation(Date), float64 Cumulative_Precipitation(Date), float64 Longitude(Date), float64 Latitude(Date)
    groups: 
D:\UC DAVIS\CW3E\data\avalanche_data\nc_Data\snotel_946_1979-10-01_2021-07-21.nc
<class 'netCDF4._netCDF4.Dataset'>
root group (NETCDF3_CLASSIC data model, file format NETCDF3):
    site_id: 946.0
    State: AK
    Elevation: 716.0
    Start Date: 1979-10-01
    dimensions(sizes): Date(15270)
    variables(dimensions): float64 Date(Date), float64 Temp_Max(Date), float64 Temp_Min(Date), float64 SWE(Date), float64 Precipitation(Date), float64 Cumulative_Precipitation(Date), float64 Longitude(Date), float64 Latitude(Date)
    groups: 
D:\U